# Basic face recognizer using pre trained model

Below the is the implementation of a very basic face recognizer which can identify the face of the person showing on a web cam.
The implementation is inspired by two path breaking papers on facial recognition using deep convoluted neural network, namely FaceNet and DeepFace.

I have used pre trained model Keras-OpenFace which is an open source Keras implementation of the OpenFace (Originally Torch implemented) 

The pretrained model that I have used is by Victor Sy Wang's implementation and was loaded using his code: https://github.com/iwantooxxoox/Keras-OpenFace.

# Import the prerequisite libraries

We will be importing utils.py from https://github.com/iwantooxxoox/Keras-OpenFace/blob/master/utils.py (available with code) which contains utility functions to create the neural network and load the weights assoiated with it.

In [1]:
from keras.models import Sequential
from keras.layers import Conv2D, ZeroPadding2D, Activation, Input, concatenate
from keras.models import Model
from keras.layers.normalization import BatchNormalization
from keras.layers.pooling import MaxPooling2D, AveragePooling2D
from keras.layers.merge import Concatenate
from keras.layers.core import Lambda, Flatten, Dense
from keras.engine.topology import Layer
from keras import backend as K
import cv2
import os
import numpy as np
from numpy import genfromtxt
import pandas as pd
import tensorflow as tf
from utils import LRN2D
import utils

%load_ext autoreload
%autoreload 2

np.set_printoptions(threshold=np.nan)

Using TensorFlow backend.


# Contructing the neural network model
The model here constructed is based on FaceNet's Inception model.

The implementation of model is available at: https://github.com/iwantooxxoox/Keras-OpenFace

In [2]:
myInput = Input(shape=(96, 96, 3))

x = ZeroPadding2D(padding=(3, 3), input_shape=(96, 96, 3))(myInput)
x = Conv2D(64, (7, 7), strides=(2, 2), name='conv1')(x)
x = BatchNormalization(axis=3, epsilon=0.00001, name='bn1')(x)
x = Activation('relu')(x)
x = ZeroPadding2D(padding=(1, 1))(x)
x = MaxPooling2D(pool_size=3, strides=2)(x)
x = Lambda(LRN2D, name='lrn_1')(x)
x = Conv2D(64, (1, 1), name='conv2')(x)
x = BatchNormalization(axis=3, epsilon=0.00001, name='bn2')(x)
x = Activation('relu')(x)
x = ZeroPadding2D(padding=(1, 1))(x)
x = Conv2D(192, (3, 3), name='conv3')(x)
x = BatchNormalization(axis=3, epsilon=0.00001, name='bn3')(x)
x = Activation('relu')(x)
x = Lambda(LRN2D, name='lrn_2')(x)
x = ZeroPadding2D(padding=(1, 1))(x)
x = MaxPooling2D(pool_size=3, strides=2)(x)

# Inception3a
inception_3a_3x3 = Conv2D(96, (1, 1), name='inception_3a_3x3_conv1')(x)
inception_3a_3x3 = BatchNormalization(axis=3, epsilon=0.00001, name='inception_3a_3x3_bn1')(inception_3a_3x3)
inception_3a_3x3 = Activation('relu')(inception_3a_3x3)
inception_3a_3x3 = ZeroPadding2D(padding=(1, 1))(inception_3a_3x3)
inception_3a_3x3 = Conv2D(128, (3, 3), name='inception_3a_3x3_conv2')(inception_3a_3x3)
inception_3a_3x3 = BatchNormalization(axis=3, epsilon=0.00001, name='inception_3a_3x3_bn2')(inception_3a_3x3)
inception_3a_3x3 = Activation('relu')(inception_3a_3x3)

inception_3a_5x5 = Conv2D(16, (1, 1), name='inception_3a_5x5_conv1')(x)
inception_3a_5x5 = BatchNormalization(axis=3, epsilon=0.00001, name='inception_3a_5x5_bn1')(inception_3a_5x5)
inception_3a_5x5 = Activation('relu')(inception_3a_5x5)
inception_3a_5x5 = ZeroPadding2D(padding=(2, 2))(inception_3a_5x5)
inception_3a_5x5 = Conv2D(32, (5, 5), name='inception_3a_5x5_conv2')(inception_3a_5x5)
inception_3a_5x5 = BatchNormalization(axis=3, epsilon=0.00001, name='inception_3a_5x5_bn2')(inception_3a_5x5)
inception_3a_5x5 = Activation('relu')(inception_3a_5x5)

inception_3a_pool = MaxPooling2D(pool_size=3, strides=2)(x)
inception_3a_pool = Conv2D(32, (1, 1), name='inception_3a_pool_conv')(inception_3a_pool)
inception_3a_pool = BatchNormalization(axis=3, epsilon=0.00001, name='inception_3a_pool_bn')(inception_3a_pool)
inception_3a_pool = Activation('relu')(inception_3a_pool)
inception_3a_pool = ZeroPadding2D(padding=((3, 4), (3, 4)))(inception_3a_pool)

inception_3a_1x1 = Conv2D(64, (1, 1), name='inception_3a_1x1_conv')(x)
inception_3a_1x1 = BatchNormalization(axis=3, epsilon=0.00001, name='inception_3a_1x1_bn')(inception_3a_1x1)
inception_3a_1x1 = Activation('relu')(inception_3a_1x1)

inception_3a = concatenate([inception_3a_3x3, inception_3a_5x5, inception_3a_pool, inception_3a_1x1], axis=3)

# Inception3b
inception_3b_3x3 = Conv2D(96, (1, 1), name='inception_3b_3x3_conv1')(inception_3a)
inception_3b_3x3 = BatchNormalization(axis=3, epsilon=0.00001, name='inception_3b_3x3_bn1')(inception_3b_3x3)
inception_3b_3x3 = Activation('relu')(inception_3b_3x3)
inception_3b_3x3 = ZeroPadding2D(padding=(1, 1))(inception_3b_3x3)
inception_3b_3x3 = Conv2D(128, (3, 3), name='inception_3b_3x3_conv2')(inception_3b_3x3)
inception_3b_3x3 = BatchNormalization(axis=3, epsilon=0.00001, name='inception_3b_3x3_bn2')(inception_3b_3x3)
inception_3b_3x3 = Activation('relu')(inception_3b_3x3)

inception_3b_5x5 = Conv2D(32, (1, 1), name='inception_3b_5x5_conv1')(inception_3a)
inception_3b_5x5 = BatchNormalization(axis=3, epsilon=0.00001, name='inception_3b_5x5_bn1')(inception_3b_5x5)
inception_3b_5x5 = Activation('relu')(inception_3b_5x5)
inception_3b_5x5 = ZeroPadding2D(padding=(2, 2))(inception_3b_5x5)
inception_3b_5x5 = Conv2D(64, (5, 5), name='inception_3b_5x5_conv2')(inception_3b_5x5)
inception_3b_5x5 = BatchNormalization(axis=3, epsilon=0.00001, name='inception_3b_5x5_bn2')(inception_3b_5x5)
inception_3b_5x5 = Activation('relu')(inception_3b_5x5)

inception_3b_pool = Lambda(lambda x: x**2, name='power2_3b')(inception_3a)
inception_3b_pool = AveragePooling2D(pool_size=(3, 3), strides=(3, 3))(inception_3b_pool)
inception_3b_pool = Lambda(lambda x: x*9, name='mult9_3b')(inception_3b_pool)
inception_3b_pool = Lambda(lambda x: K.sqrt(x), name='sqrt_3b')(inception_3b_pool)
inception_3b_pool = Conv2D(64, (1, 1), name='inception_3b_pool_conv')(inception_3b_pool)
inception_3b_pool = BatchNormalization(axis=3, epsilon=0.00001, name='inception_3b_pool_bn')(inception_3b_pool)
inception_3b_pool = Activation('relu')(inception_3b_pool)
inception_3b_pool = ZeroPadding2D(padding=(4, 4))(inception_3b_pool)

inception_3b_1x1 = Conv2D(64, (1, 1), name='inception_3b_1x1_conv')(inception_3a)
inception_3b_1x1 = BatchNormalization(axis=3, epsilon=0.00001, name='inception_3b_1x1_bn')(inception_3b_1x1)
inception_3b_1x1 = Activation('relu')(inception_3b_1x1)

inception_3b = concatenate([inception_3b_3x3, inception_3b_5x5, inception_3b_pool, inception_3b_1x1], axis=3)

# Inception3c
inception_3c_3x3 = utils.conv2d_bn(inception_3b,
                                   layer='inception_3c_3x3',
                                   cv1_out=128,
                                   cv1_filter=(1, 1),
                                   cv2_out=256,
                                   cv2_filter=(3, 3),
                                   cv2_strides=(2, 2),
                                   padding=(1, 1))

inception_3c_5x5 = utils.conv2d_bn(inception_3b,
                                   layer='inception_3c_5x5',
                                   cv1_out=32,
                                   cv1_filter=(1, 1),
                                   cv2_out=64,
                                   cv2_filter=(5, 5),
                                   cv2_strides=(2, 2),
                                   padding=(2, 2))

inception_3c_pool = MaxPooling2D(pool_size=3, strides=2)(inception_3b)
inception_3c_pool = ZeroPadding2D(padding=((0, 1), (0, 1)))(inception_3c_pool)

inception_3c = concatenate([inception_3c_3x3, inception_3c_5x5, inception_3c_pool], axis=3)

#inception 4a
inception_4a_3x3 = utils.conv2d_bn(inception_3c,
                                   layer='inception_4a_3x3',
                                   cv1_out=96,
                                   cv1_filter=(1, 1),
                                   cv2_out=192,
                                   cv2_filter=(3, 3),
                                   cv2_strides=(1, 1),
                                   padding=(1, 1))
inception_4a_5x5 = utils.conv2d_bn(inception_3c,
                                   layer='inception_4a_5x5',
                                   cv1_out=32,
                                   cv1_filter=(1, 1),
                                   cv2_out=64,
                                   cv2_filter=(5, 5),
                                   cv2_strides=(1, 1),
                                   padding=(2, 2))

inception_4a_pool = Lambda(lambda x: x**2, name='power2_4a')(inception_3c)
inception_4a_pool = AveragePooling2D(pool_size=(3, 3), strides=(3, 3))(inception_4a_pool)
inception_4a_pool = Lambda(lambda x: x*9, name='mult9_4a')(inception_4a_pool)
inception_4a_pool = Lambda(lambda x: K.sqrt(x), name='sqrt_4a')(inception_4a_pool)
inception_4a_pool = utils.conv2d_bn(inception_4a_pool,
                                   layer='inception_4a_pool',
                                   cv1_out=128,
                                   cv1_filter=(1, 1),
                                   padding=(2, 2))
inception_4a_1x1 = utils.conv2d_bn(inception_3c,
                                   layer='inception_4a_1x1',
                                   cv1_out=256,
                                   cv1_filter=(1, 1))
inception_4a = concatenate([inception_4a_3x3, inception_4a_5x5, inception_4a_pool, inception_4a_1x1], axis=3)

#inception4e
inception_4e_3x3 = utils.conv2d_bn(inception_4a,
                                   layer='inception_4e_3x3',
                                   cv1_out=160,
                                   cv1_filter=(1, 1),
                                   cv2_out=256,
                                   cv2_filter=(3, 3),
                                   cv2_strides=(2, 2),
                                   padding=(1, 1))
inception_4e_5x5 = utils.conv2d_bn(inception_4a,
                                   layer='inception_4e_5x5',
                                   cv1_out=64,
                                   cv1_filter=(1, 1),
                                   cv2_out=128,
                                   cv2_filter=(5, 5),
                                   cv2_strides=(2, 2),
                                   padding=(2, 2))
inception_4e_pool = MaxPooling2D(pool_size=3, strides=2)(inception_4a)
inception_4e_pool = ZeroPadding2D(padding=((0, 1), (0, 1)))(inception_4e_pool)

inception_4e = concatenate([inception_4e_3x3, inception_4e_5x5, inception_4e_pool], axis=3)

#inception5a
inception_5a_3x3 = utils.conv2d_bn(inception_4e,
                                   layer='inception_5a_3x3',
                                   cv1_out=96,
                                   cv1_filter=(1, 1),
                                   cv2_out=384,
                                   cv2_filter=(3, 3),
                                   cv2_strides=(1, 1),
                                   padding=(1, 1))

inception_5a_pool = Lambda(lambda x: x**2, name='power2_5a')(inception_4e)
inception_5a_pool = AveragePooling2D(pool_size=(3, 3), strides=(3, 3))(inception_5a_pool)
inception_5a_pool = Lambda(lambda x: x*9, name='mult9_5a')(inception_5a_pool)
inception_5a_pool = Lambda(lambda x: K.sqrt(x), name='sqrt_5a')(inception_5a_pool)
inception_5a_pool = utils.conv2d_bn(inception_5a_pool,
                                   layer='inception_5a_pool',
                                   cv1_out=96,
                                   cv1_filter=(1, 1),
                                   padding=(1, 1))
inception_5a_1x1 = utils.conv2d_bn(inception_4e,
                                   layer='inception_5a_1x1',
                                   cv1_out=256,
                                   cv1_filter=(1, 1))

inception_5a = concatenate([inception_5a_3x3, inception_5a_pool, inception_5a_1x1], axis=3)

#inception_5b
inception_5b_3x3 = utils.conv2d_bn(inception_5a,
                                   layer='inception_5b_3x3',
                                   cv1_out=96,
                                   cv1_filter=(1, 1),
                                   cv2_out=384,
                                   cv2_filter=(3, 3),
                                   cv2_strides=(1, 1),
                                   padding=(1, 1))
inception_5b_pool = MaxPooling2D(pool_size=3, strides=2)(inception_5a)
inception_5b_pool = utils.conv2d_bn(inception_5b_pool,
                                   layer='inception_5b_pool',
                                   cv1_out=96,
                                   cv1_filter=(1, 1))
inception_5b_pool = ZeroPadding2D(padding=(1, 1))(inception_5b_pool)

inception_5b_1x1 = utils.conv2d_bn(inception_5a,
                                   layer='inception_5b_1x1',
                                   cv1_out=256,
                                   cv1_filter=(1, 1))
inception_5b = concatenate([inception_5b_3x3, inception_5b_pool, inception_5b_1x1], axis=3)

av_pool = AveragePooling2D(pool_size=(3, 3), strides=(1, 1))(inception_5b)
reshape_layer = Flatten()(av_pool)
dense_layer = Dense(128, name='dense_layer')(reshape_layer)
norm_layer = Lambda(lambda  x: K.l2_normalize(x, axis=1), name='norm_layer')(dense_layer)


# Final Model
model = Model(inputs=[myInput], outputs=norm_layer)

# Loading the model with pretrained weights

FaceNet is trained by minimizing the triplet loss. I will be  loading a previously trained model. weights are avaiable at https://github.com/iwantooxxoox/Keras-OpenFace in the "weights" folder which is also provided in this source.

This can take a couple of minutes to execute and depends on the speed of your machine.


In [3]:
# Load weights from csv files (which was exported from Openface torch model)
weights = utils.weights
weights_dict = utils.load_weights()

# Set layer weights of the model
for name in weights:
  if model.get_layer(name) != None:
    model.get_layer(name).set_weights(weights_dict[name])
  elif model.get_layer(name) != None:
    model.get_layer(name).set_weights(weights_dict[name])

## About <font color=blue>image_to_embedding</font> function        
When the model is loaded with pre trained weights, then we can create the **128 dimensional embedding vectors** for all the face images stored in the "images" folder. **"image_to_embedding"** function pass an image to the Inception network to generate the embedding vector.

In [4]:
def image_to_embedding(image, model):
    #image = cv2.resize(image, (96, 96), interpolation=cv2.INTER_AREA) 
    image = cv2.resize(image, (96, 96)) 
    img = image[...,::-1]
    img = np.around(np.transpose(img, (0,1,2))/255.0, decimals=12)
    x_train = np.array([img])
    embedding = model.predict_on_batch(x_train)
    return embedding


## About <font color=blue>recognize_face</font> function
This function calculate similarity between the captured image and the images that are already been stored. It passes the image to the trained neural network to generate its embedding vector. Which is then compared with all the embedding vectors of the images stored by calculating L2 Euclidean distance. 

If the minimum L2 distance between two embeddings is less than a threshpld (here I have taken the threashhold as .68 (which can be adjusted) then we have a match.

In [26]:
def recognize_face(face_image, input_embeddings, model):

    embedding = image_to_embedding(face_image, model)
    
    minimum_distance = 200
    name = None
    
    # Loop over  names and encodings.
    for (input_name, input_embedding) in input_embeddings.items():
        
       
        euclidean_distance = np.linalg.norm(embedding-input_embedding)
        

        print('Euclidean distance from %s is %s' %(input_name.split('_')[0], euclidean_distance))

        
        if euclidean_distance < minimum_distance:
            minimum_distance = euclidean_distance
            name = input_name
    
    if minimum_distance < 0.8:
        return str(name)
    else:
        return None

## About <font color=blue>create_input_image_embeddings</font> function
This function generates 128 dimensional image ebeddings of all the images stored in the "images" directory by feed forwarding the images to a trained neural network. It creates a dictionary with key as the name of the face and value as embedding


## About <font color=blue>recognize_faces_in_cam</font> function
This function capture image from the webcam, detect a face in it and crop the image to have a face only, which is then passed to recognize_face function. 

In [28]:
import glob

def create_input_image_embeddings():
    input_embeddings = {}

    for file in glob.glob("images/*"):
        person_name = os.path.splitext(os.path.basename(file))[0]
        image_file = cv2.imread(file, 1)
        input_embeddings[person_name] = image_to_embedding(image_file, model)

    return input_embeddings

def recognize_faces_in_cam(input_embeddings):
    

    cv2.namedWindow("Face Recognizer")
    vc = cv2.VideoCapture(0)
   

    font = cv2.FONT_HERSHEY_SIMPLEX
    face_cascade = cv2.CascadeClassifier('haarcascade_frontalface_default.xml')
    
    
    while vc.isOpened():
        _, frame = vc.read()
        img = frame
        height, width, channels = frame.shape

        
        
        gray = cv2.cvtColor(frame, cv2.COLOR_BGR2GRAY)
        faces = face_cascade.detectMultiScale(gray, 1.3, 5)

        # Loop through all the faces detected 
        identities = []
        for (x, y, w, h) in faces:
            x1 = x
            y1 = y
            x2 = x+w
            y2 = y+h

           
            
            face_image = frame[max(0, y1):min(height, y2), max(0, x1):min(width, x2)]    
            identity = recognize_face(face_image, input_embeddings, model)
            
            

            if identity is not None:
                img = cv2.rectangle(frame,(x1, y1),(x2, y2),(255,255,255),2)
                cv2.putText(img, str(identity.split('_')[0]), (x1+5,y1-5), font, 1, (255,255,255), 2)
        
        key = cv2.waitKey(100)
        cv2.imshow("Face Recognizer", img)

        if key == 27: # exit on ESC
            break
    vc.release()
    cv2.destroyAllWindows()

## Capturing the face image
Following code captures 10 face images of the person. They all are stored in **"images"** folder with the name User_1 to User_10. Select a good captured image from the set of 10 images. Rename it with the name of person and delete rest of them. This image will be used for recognizing the the identity of the person using one shot learning.

In [53]:
cam = cv2.VideoCapture(0)

face_detector = cv2.CascadeClassifier('haarcascade_frontalface_default.xml')

count = 0
while(True):
    ret, img = cam.read()
    #gray = cv2.cvtColor(img, cv2.COLOR_BGR2GRAY)
    faces = face_detector.detectMultiScale(img, 1.3, 5)
    for (x,y,w,h) in faces:
        x1 = x
        y1 = y
        x2 = x+w
        y2 = y+h
        cv2.rectangle(img, (x1,y1), (x2,y2), (255,255,255), 2)     
        count += 1
        # Save the captured image into the datasets folder
        cv2.imwrite("images/Anurag_" + str(count) + ".jpg", img[y1:y2,x1:x2])
        cv2.imshow('image', img)
    k = cv2.waitKey(1000) & 0xff # Press 'ESC' for exiting video
    if k == 27:
        break
    elif count >= 10: # Take 30 face sample and stop video
         break
cam.release()
cv2.destroyAllWindows()

# Lets run the face recognizer program :-)

In [54]:
input_embeddings = create_input_image_embeddings()
recognize_faces_in_cam(input_embeddings)


Euclidean distance from Ankur is 1.06901
Euclidean distance from Ankur is 1.18877
Euclidean distance from Ankur is 1.12839
Euclidean distance from Ankur is 1.12911
Euclidean distance from Ankur is 1.15311
Euclidean distance from Ankur is 1.16983
Euclidean distance from Ankur is 1.18715
Euclidean distance from Ankur is 1.21553
Euclidean distance from Ankur is 1.22611
Euclidean distance from Ankur is 1.18423
Euclidean distance from Anurag1 is 0.934713
Euclidean distance from Anurag10 is 0.983534
Euclidean distance from Anurag2 is 0.995093
Euclidean distance from Anurag3 is 0.999595
Euclidean distance from Anurag4 is 0.924996
Euclidean distance from Anurag5 is 0.937655
Euclidean distance from Anurag6 is 1.15011
Euclidean distance from Anurag7 is 1.27921
Euclidean distance from Anurag8 is 1.13872
Euclidean distance from Anurag9 is 1.009
Euclidean distance from Anurag is 0.684469
Euclidean distance from Anurag is 0.743233
Euclidean distance from Anurag is 0.733581
Euclidean distance from An

Euclidean distance from Ankur is 0.898399
Euclidean distance from Ankur is 1.01939
Euclidean distance from Ankur is 1.00169
Euclidean distance from Ankur is 0.9779
Euclidean distance from Ankur is 1.01379
Euclidean distance from Ankur is 0.969216
Euclidean distance from Ankur is 1.07163
Euclidean distance from Ankur is 1.04846
Euclidean distance from Ankur is 1.03899
Euclidean distance from Ankur is 1.00981
Euclidean distance from Anurag1 is 0.691303
Euclidean distance from Anurag10 is 0.756618
Euclidean distance from Anurag2 is 0.72016
Euclidean distance from Anurag3 is 0.819934
Euclidean distance from Anurag4 is 0.753742
Euclidean distance from Anurag5 is 0.759442
Euclidean distance from Anurag6 is 0.953081
Euclidean distance from Anurag7 is 1.07585
Euclidean distance from Anurag8 is 0.892819
Euclidean distance from Anurag9 is 0.792875
Euclidean distance from Anurag is 0.574794
Euclidean distance from Anurag is 0.797184
Euclidean distance from Anurag is 0.638004
Euclidean distance fr

Euclidean distance from Ankur is 0.801158
Euclidean distance from Ankur is 0.87182
Euclidean distance from Ankur is 0.892334
Euclidean distance from Ankur is 0.876069
Euclidean distance from Ankur is 0.907175
Euclidean distance from Ankur is 0.871412
Euclidean distance from Ankur is 0.970163
Euclidean distance from Ankur is 0.882171
Euclidean distance from Ankur is 0.898623
Euclidean distance from Ankur is 0.898589
Euclidean distance from Anurag1 is 0.602024
Euclidean distance from Anurag10 is 0.587545
Euclidean distance from Anurag2 is 0.521396
Euclidean distance from Anurag3 is 0.759592
Euclidean distance from Anurag4 is 0.697994
Euclidean distance from Anurag5 is 0.703149
Euclidean distance from Anurag6 is 0.798743
Euclidean distance from Anurag7 is 0.854659
Euclidean distance from Anurag8 is 0.678294
Euclidean distance from Anurag9 is 0.614626
Euclidean distance from Anurag is 0.840283
Euclidean distance from Anurag is 1.09462
Euclidean distance from Anurag is 0.849741
Euclidean di

Euclidean distance from Ankur is 0.790995
Euclidean distance from Ankur is 0.837019
Euclidean distance from Ankur is 0.86434
Euclidean distance from Ankur is 0.849652
Euclidean distance from Ankur is 0.892879
Euclidean distance from Ankur is 0.859576
Euclidean distance from Ankur is 0.929777
Euclidean distance from Ankur is 0.846553
Euclidean distance from Ankur is 0.860187
Euclidean distance from Ankur is 0.868824
Euclidean distance from Anurag1 is 0.614229
Euclidean distance from Anurag10 is 0.636929
Euclidean distance from Anurag2 is 0.540339
Euclidean distance from Anurag3 is 0.771448
Euclidean distance from Anurag4 is 0.73009
Euclidean distance from Anurag5 is 0.722713
Euclidean distance from Anurag6 is 0.745853
Euclidean distance from Anurag7 is 0.789197
Euclidean distance from Anurag8 is 0.648917
Euclidean distance from Anurag9 is 0.66169
Euclidean distance from Anurag is 0.867084
Euclidean distance from Anurag is 1.12726
Euclidean distance from Anurag is 0.901269
Euclidean dist

Euclidean distance from Krish is 1.06034
Euclidean distance from Krish is 1.01346
Euclidean distance from Krish is 0.95431
Euclidean distance from Perumal is 0.894357
Euclidean distance from Perumal is 0.910524
Euclidean distance from Perumal is 0.864033
Euclidean distance from Perumal is 0.810759
Euclidean distance from Perumal is 0.885163
Euclidean distance from Perumal is 1.00207
Euclidean distance from Perumal is 1.02329
Euclidean distance from Perumal is 0.989009
Euclidean distance from Perumal is 1.05803
Euclidean distance from Perumal is 0.952845
Euclidean distance from Pranoy is 0.945544
Euclidean distance from Pranoy is 0.901637
Euclidean distance from Pranoy is 0.892966
Euclidean distance from Pranoy is 1.01571
Euclidean distance from Pranoy is 0.986285
Euclidean distance from Pranoy is 1.02148
Euclidean distance from Pranoy is 1.02843
Euclidean distance from Pranoy is 0.959332
Euclidean distance from Pranoy is 0.926171
Euclidean distance from Pranoy is 0.909463
Euclidean dis

...

Euclidean distance from Ankur is 0.815085
Euclidean distance from Ankur is 0.878229
Euclidean distance from Ankur is 0.881369
Euclidean distance from Ankur is 0.875146
Euclidean distance from Ankur is 0.907185
Euclidean distance from Ankur is 0.916627
Euclidean distance from Ankur is 0.946294
Euclidean distance from Ankur is 0.887348
Euclidean distance from Ankur is 0.92403
Euclidean distance from Ankur is 0.918866
Euclidean distance from Anurag1 is 0.702844
Euclidean distance from Anurag10 is 0.675469
Euclidean distance from Anurag2 is 0.652887
Euclidean distance from Anurag3 is 0.863983
Euclidean distance from Anurag4 is 0.811705
Euclidean distance from Anurag5 is 0.803455
Euclidean distance from Anurag6 is 0.798977
Euclidean distance from Anurag7 is 0.843424
Euclidean distance from Anurag8 is 0.734143
Euclidean distance from Anurag9 is 0.705837
Euclidean distance from Anurag is 0.839466
Euclidean distance from Anurag is 1.12979
Euclidean distance from Anurag is 0.946448
Euclidean di

Euclidean distance from Ankur is 0.917763
Euclidean distance from Ankur is 0.86461
Euclidean distance from Ankur is 0.93423
Euclidean distance from Ankur is 0.945098
Euclidean distance from Ankur is 1.01986
Euclidean distance from Ankur is 1.00019
Euclidean distance from Ankur is 0.996431
Euclidean distance from Ankur is 0.927965
Euclidean distance from Ankur is 0.961555
Euclidean distance from Ankur is 0.934384
Euclidean distance from Anurag1 is 0.840948
Euclidean distance from Anurag10 is 0.942228
Euclidean distance from Anurag2 is 0.833026
Euclidean distance from Anurag3 is 1.0216
Euclidean distance from Anurag4 is 0.990052
Euclidean distance from Anurag5 is 0.967406
Euclidean distance from Anurag6 is 0.851008
Euclidean distance from Anurag7 is 0.797335
Euclidean distance from Anurag8 is 0.869965
Euclidean distance from Anurag9 is 0.964983
Euclidean distance from Anurag is 1.10827
Euclidean distance from Anurag is 1.28612
Euclidean distance from Anurag is 1.15386
Euclidean distance 

Euclidean distance from Ankur is 0.983113
Euclidean distance from Ankur is 0.973117
Euclidean distance from Ankur is 1.03685
Euclidean distance from Ankur is 1.04234
Euclidean distance from Ankur is 1.10421
Euclidean distance from Ankur is 1.05774
Euclidean distance from Ankur is 1.12106
Euclidean distance from Ankur is 1.0342
Euclidean distance from Ankur is 1.04282
Euclidean distance from Ankur is 1.02345
Euclidean distance from Anurag1 is 0.684211
Euclidean distance from Anurag10 is 0.834165
Euclidean distance from Anurag2 is 0.723275
Euclidean distance from Anurag3 is 0.935108
Euclidean distance from Anurag4 is 0.858122
Euclidean distance from Anurag5 is 0.869389
Euclidean distance from Anurag6 is 0.915628
Euclidean distance from Anurag7 is 0.891971
Euclidean distance from Anurag8 is 0.857897
Euclidean distance from Anurag9 is 0.87636
Euclidean distance from Anurag is 0.992171
Euclidean distance from Anurag is 1.19246
Euclidean distance from Anurag is 0.989293
Euclidean distance fr

Euclidean distance from Ankur is 0.945828
Euclidean distance from Ankur is 0.891088
Euclidean distance from Ankur is 0.934309
Euclidean distance from Ankur is 0.956909
Euclidean distance from Ankur is 1.02744
Euclidean distance from Ankur is 1.05738
Euclidean distance from Ankur is 0.976016
Euclidean distance from Ankur is 0.943494
Euclidean distance from Ankur is 0.992765
Euclidean distance from Ankur is 0.955183
Euclidean distance from Anurag1 is 0.980285
Euclidean distance from Anurag10 is 1.04694
Euclidean distance from Anurag2 is 0.981456
Euclidean distance from Anurag3 is 1.12222
Euclidean distance from Anurag4 is 1.09692
Euclidean distance from Anurag5 is 1.07797
Euclidean distance from Anurag6 is 0.911445
Euclidean distance from Anurag7 is 0.852154
Euclidean distance from Anurag8 is 0.996983
Euclidean distance from Anurag9 is 1.06432
Euclidean distance from Anurag is 1.19629
Euclidean distance from Anurag is 1.33898
Euclidean distance from Anurag is 1.26543
Euclidean distance f

Euclidean distance from Ankur is 0.770229
Euclidean distance from Ankur is 0.78434
Euclidean distance from Ankur is 0.816622
Euclidean distance from Ankur is 0.823204
Euclidean distance from Ankur is 0.882329
Euclidean distance from Ankur is 0.879692
Euclidean distance from Ankur is 0.892904
Euclidean distance from Ankur is 0.819721
Euclidean distance from Ankur is 0.865367
Euclidean distance from Ankur is 0.850387
Euclidean distance from Anurag1 is 0.699448
Euclidean distance from Anurag10 is 0.738182
Euclidean distance from Anurag2 is 0.653034
Euclidean distance from Anurag3 is 0.880412
Euclidean distance from Anurag4 is 0.828166
Euclidean distance from Anurag5 is 0.806491
Euclidean distance from Anurag6 is 0.770301
Euclidean distance from Anurag7 is 0.791624
Euclidean distance from Anurag8 is 0.749533
Euclidean distance from Anurag9 is 0.754912
Euclidean distance from Anurag is 0.944132
Euclidean distance from Anurag is 1.18391
Euclidean distance from Anurag is 1.0144
Euclidean dist

In [ ]:
for file in glob.glob("images/Train/*"):
    person_name = os.path.splitext(os.path.basename(file))[0]
    print(person_name)
    image_file = cv2.imread(file, 1)

In [ ]:
os.path.splitext('Anurag')[0]